In [2]:
import pandas as pd
import re

text_df = pd.read_csv('gutenberg/gutenberg_raw.csv')

text_df.head()

author           title                                               vers
0  alexis      Entführung  O Lady Judith, spröder Schatz,\n        Drückt...
1  alexis      Entführung  Hart ist der Sitz und knapp und schmal,\n     ...
2  alexis      Entführung  Sechs Nächte lag ich in Sumpf und Moor\n      ...
3  alexis  Walpurgisnacht  Liebe Mutter, heut' Nacht heulte Regen und Win...
4  alexis  Walpurgisnacht  Liebe Mutter, es donnerte auf dem Brocken drob...

In [2]:
verse_name = 'vers'

# Preprocessing for Bert Training

In [5]:
# EOV: End of verse; SOV: Start of Verse; SST: Start of Strophe; EST: End of Strophe
# SOP: Start of poem; EOP: End of Poem

text_df_prep = text_df.copy()
text_df_prep[verse_name] = text_df_prep[verse_name].apply(lambda x: re.sub(r'[^a-zäöüA-ZÄÖÜ,.\n]',' ', str(x)))
text_df_prep[verse_name] = text_df_prep[verse_name].apply(lambda x: (' [EOV] [SOV] ').join([line.lstrip() for line in str(x).split('\n') if line] )+ ' [EST] ')

#text_df_prep = text_df_prep.groupby(['title']).sum()



text = ''
for _, row in text_df_prep.iterrows():
    
    text += row[verse_name]
    
with open('bert_training_gutenberg.txt', 'w') as f:
    f.write(text)

# Preprocessing for GPT2 Training

In [3]:
text_df = pd.read_csv('gutenberg/gutenberg_filtered.csv')

text_df.head()

ID  author           title subtitle  \
0   0  alexis      Entführung      NaN   
1   0  alexis      Entführung      NaN   
2   0  alexis      Entführung      NaN   
3   1  alexis  Walpurgisnacht      NaN   
4   1  alexis  Walpurgisnacht      NaN   

                                                vers  
0  O Lady Judith, spröder Schatz,\n        Drückt...  
1  Hart ist der Sitz und knapp und schmal,\n     ...  
2  Sechs Nächte lag ich in Sumpf und Moor\n      ...  
3  Liebe Mutter, heut' Nacht heulte Regen und Win...  
4  Liebe Mutter, es donnerte auf dem Brocken drob...

In [4]:
title_name = 'title'
verse_name = 'vers'


text_df_prep = text_df.copy()
text_df_prep[verse_name] = text_df_prep[verse_name].apply(lambda x: re.sub(r'[^a-zäöüA-ZÄÖÜ,;:.\n ]','', str(x)))
text_df_prep[verse_name] = text_df_prep[verse_name].apply(lambda x: ('\n').join([line.lstrip() for line in str(x).split('\n') if line] )+ '\n')

text_df_strophes = text_df_prep.groupby(['ID']).sum()[verse_name]

text_df_titles = text_df_prep.groupby(['ID']).first()[title_name]

strophes_df = pd.concat([text_df_titles, text_df_strophes], axis=1)

text = ''
for _ , row in strophes_df.iterrows():
    
    text += 'Titel: ' + str(row[title_name]) + '\n \n' + row[verse_name] + '\n [EOP]'
    
    
    
with open('gpt2_training_gutenberg.txt', 'w') as f:
    f.write(text)

In [5]:
text

'Titel: Entführung\n \nO Lady Judith, spröder Schatz,\nDrückt dich zu fest mein Arm\nJe zwei zu Pferd haben schlechten Platz\nUnd Winternacht weht nicht warm. \n\nHart ist der Sitz und knapp und schmal,\nUnd kalt mein Kleid von Erz,\nDoch kälter und härter als Sattel und Stahl\nWar gegen mich dein Herz.\nSechs Nächte lag ich in Sumpf und Moor\nUnd hab um dich gewacht,\nDoch weicher, bei Sankt Görg ichs schwor,\nSchlaf ich die siebente Nacht\n\n [EOP]Titel: Walpurgisnacht\n \nLiebe Mutter, heut Nacht heulte Regen und Wind.\nIst heute der erste Mai, liebes Kind. \n\nLiebe Mutter, es donnerte auf dem Brocken droben.\nLiebes Kind, es waren die Hexen oben.\nLiebe Mutter, ich möcht keine Hexen sehn.\nLiebes Kind, es ist wohl schon oft geschehn.\nLiebe Mutter, ob wohl im Dorf Hexen sind\nSie sind dir wohl näher, mein liebes Kind.\nLiebe Mutter, worauf fliegen die Hexen zum Berg\nLiebes Kind, auf dem Rauche von heissem Werg.\nLiebe Mutter, worauf reiten die Hexen zum Spiel\nLiebes Kind, sie re